# AIR - Exercise in Google Colab

## Colab Preparation

Open via google drive -> right click: open with Colab

**Get a GPU**

Toolbar -> Runtime -> Change Runtime Type -> GPU

**Mount Google Drive**

* Download data and clone your github repo to your Google Drive folder
* Use Google Drive as connection between Github and Colab (Could also use direct github access, but re-submitting credentials might be annoying)
* Commit to Github locally from the synced drive

**Keep Alive**

When training google colab tends to kick you out, This might help: https://medium.com/@shivamrawat_756/how-to-prevent-google-colab-from-disconnecting-717b88a128c0

**Get Started**

Run the following script to mount google drive and install needed python packages. Pytorch comes pre-installed.

In [33]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [34]:
cd /content/drive/MyDrive/air-2022-group-06-main

/content/drive/MyDrive/air-2022-group-06-main


In [ ]:
!pip install -r requirements.txt

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 505 kB 14.1 MB/s 
     |████████████████████████████████| 248 kB 86.7 MB/s 
     |████████████████████████████████| 269 kB 71.4 MB/s 
     |████████████████████████████████| 748.8 MB 16 kB/s 
     |████████████████████████████████| 1.3 MB 64.6 MB/s 
     |████████████████████████████████| 592 kB 81.1 MB/s 
     |████████████████████████████████| 132 kB 86.1 MB/s 
     |████████████████████████████████| 125 kB 81.5 MB/s 
     |████████████████████████████████| 1.1 MB 67.0 MB/s 
     |████████████████████████████████| 880 kB 83.4 MB/s 
     |████████████████████████████████| 2.9 MB 75.4 MB/s 
     |████████████████████████████████| 79 kB 8.8 MB/s 
     |████████████████████████████████| 8.9 MB 88.2 MB/s 
     |████████████████████████████████| 138 kB 87.3 MB/s 
     |████████████████████████████████| 127 kB 73.2 MB/s 
  Created wheel for PyYAML: filen

In [ ]:
import torch

print("Version:",torch.__version__)
print("Has GPU:",torch.cuda.is_available()) # check that 1 gpu is available
print("Random tensor:",torch.rand(10,device="cuda")) # check that pytorch works 

Version: 1.6.0
Has GPU: True
Random tensor: tensor([0.3955, 0.8023, 0.9986, 0.3422, 0.9890, 0.8893, 0.2506, 0.7493, 0.2661,
        0.5336], device='cuda:0')


# Main.py Replacement

-> add your code here

- Replace *air_test* with your google drive location in the sys.path.append()

In [ ]:
from allennlp.common import Params, Tqdm
from allennlp.common.util import prepare_environment
from allennlp.data.dataloader import PyTorchDataLoader
prepare_environment(Params({})) # sets the seeds to be fixed

import torch

from allennlp.data.vocabulary import Vocabulary

from allennlp.modules.token_embedders import Embedding
from allennlp.modules.text_field_embedders import BasicTextFieldEmbedder
from torch.optim import Adam
import time
from allennlp.nn.util import move_to_device

In [35]:
cd src/

/content/drive/MyDrive/air-2022-group-06-main/src


In [36]:
ls

core_metrics.py      extractive_qa.py          model_knrm.py     re_ranking.py
data_loading.py      judgement_aggregation.py  model_tk.py
extractive_qa.ipynb  model_conv_knrm.py        re_ranking.ipynb


In [ ]:
from data_loading import *
from model_knrm import *
from model_conv_knrm import *
from model_tk import *
from early_stopper import EarlyStopping
from validation import *
from msmarco_eval import *

In [ ]:
# change paths to your data directory
config = {
    "vocab_directory": "/content/drive/My Drive/air-2022-group-06-main/data/allen_vocab_lower_10",
    "pre_trained_embedding": "/content/drive/My Drive/air-2022-group-06-main/data/glove.42B.300d.txt", 
    "model": "conv_knrm",
    "train_data": "/content/drive/My Drive/air-2022-group-06-main/data/triples.train.tsv",
    "validation_data": "/content/drive/My Drive/air-2022-group-06-main/data/msmarco_tuples.validation.tsv",
    "test_data":"/content/drive/My Drive/air-2022-group-06-main/data/msmarco_tuples.test.tsv",
}

Data loading

In [ ]:
#
# data loading
#

vocab = Vocabulary.from_files(config["vocab_directory"])
tokens_embedder = Embedding(vocab=vocab,
                           pretrained_file= config["pre_trained_embedding"],
                           embedding_dim=300,
                           trainable=True,
                           padding_index=0)
word_embedder = BasicTextFieldEmbedder({"tokens": tokens_embedder})

1917494it [00:18, 104204.00it/s]


Recomended paramters for models

In [ ]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [ ]:
device.type

'cuda'

In [ ]:
# recommended default params for the models (but you may change them if you want)
if config["model"] == "knrm":
    model = KNRM(word_embedder, n_kernels=11).to(device)
elif config["model"] == "conv_knrm":
    model = Conv_KNRM(word_embedder, n_grams=3, n_kernels=11, conv_out_dim=128).to(device)
elif config["model"] == "tk":
    model = TK(word_embedder, n_kernels=11, n_layers = 2, n_tf_dim = 300, n_tf_heads = 10).to(device)

todo optimizer, loss

In [ ]:
optimizer = Adam(model.parameters(), lr=0.001, weight_decay=0)
criterion = torch.nn.MarginRankingLoss(margin=1, reduction='mean').to(device)
print('Model',config["model"],'total parameters:', sum(p.numel() for p in model.parameters() if p.requires_grad))
print('Network:', model)

Model conv_knrm total parameters: 94613283
Network: Conv_KNRM(
  (word_embeddings): BasicTextFieldEmbedder(
    (token_embedder_tokens): Embedding()
  )
  (convolutions): ModuleList(
    (0): Sequential(
      (0): ConstantPad1d(padding=(0, 0), value=0)
      (1): Conv1d(300, 128, kernel_size=(1,), stride=(1,))
      (2): ReLU()
    )
    (1): Sequential(
      (0): ConstantPad1d(padding=(0, 1), value=0)
      (1): Conv1d(300, 128, kernel_size=(2,), stride=(1,))
      (2): ReLU()
    )
    (2): Sequential(
      (0): ConstantPad1d(padding=(0, 2), value=0)
      (1): Conv1d(300, 128, kernel_size=(3,), stride=(1,))
      (2): ReLU()
    )
  )
  (cosine_module): CosineMatrixAttention()
  (dense): Linear(in_features=99, out_features=1, bias=False)
)


Train

In [ ]:
_triple_reader = IrTripleDatasetReader(lazy=True, max_doc_length=180, max_query_length=30)
_triple_reader = _triple_reader.read(config["train_data"])
_triple_reader.index_with(vocab)
loader = PyTorchDataLoader(_triple_reader, batch_size=32)

In [ ]:
from pathlib import Path
from datetime import datetime


def print_and_store_loss(epoch: int, batch: int, loss_sum, model_name: str):
    store_loss_path = Path(f'../output_loss/{model_name}_loss.txt')

    output = f'Time: {datetime.now().isoformat()}, Epoch: {epoch}, batch: {batch}, loss: {loss_sum.item() }'  # removed /100

    if batch % 100 == 0:
        with open(store_loss_path, 'a') as loss:
            loss.write(f'{output} \n')

    elif batch % 100 == 0:
        print(output)


In [23]:

TRAINING_BATCH_SIZE = 256
MAX_DOC_LENGTH = 180
MAX_QUERY_LENGTH = 30
PATIENCE_EARLY_STOP = 15
NO_OF_BATCHES_TO_VALIDATE = 2000
early_stopper = EarlyStopping(patience=PATIENCE_EARLY_STOP, mode='max')

best_metric_info = {
    'metrics': {
        'MRR @10': 0
    }
}

label = torch.ones(TRAINING_BATCH_SIZE).to(device)
loss_sum = torch.zeros(1).to(device)
START_TIME = time.time()
for epoch in range(2):

    for i, batch in enumerate(Tqdm.tqdm(loader)):
        current_batch_size = len(batch['query_tokens']['tokens'])

        if device.type == 'cuda':
            batch = move_to_device(batch, device.index)

        optimizer.zero_grad()

        # with torch.to.stream(s_pos):
        output_pos = model.forward(query = batch.get("query_tokens"),
                                   document = batch.get("doc_pos_tokens"))
        # with torch.to.stream(s_neg):
        output_neg = model.forward(query = batch.get("query_tokens"),
                                   document = batch.get("doc_neg_tokens"))

        # Since the last batch might be smaller we are checking its size
        if current_batch_size != TRAINING_BATCH_SIZE:
            label = torch.ones(current_batch_size).to(device)

        loss = criterion(output_pos, output_neg, label)
        loss.backward()

        optimizer.step()

        # for next iteration we set the label back to a cached version
        if current_batch_size != TRAINING_BATCH_SIZE:
            label = torch.ones(TRAINING_BATCH_SIZE).to(device)

        loss_sum = loss_sum.data + loss.detach().data
        print_and_store_loss(epoch, i, loss_sum, config['model'])

        loss_sum = torch.zeros(1).to(device)

        # perform validation during training process
        if i != 0 and i % NO_OF_BATCHES_TO_VALIDATE == 0:
            best_metric = validate_model(model,
                                         config,
                                         epoch,
                                         i,
                                         device)

            if best_metric['metrics']['MRR @10'] > best_metric_info['metrics']['MRR @10']:
                best_metric_info = best_metric

            model.train()
            if early_stopper.step(best_metric['metrics']['MRR @10']):
                print("early stopping epoch %i batch count %i", epoch, i)
                break

END = time.time()

0it [00:00, ?it/s]
reading instances: 0it [00:00, ?it/s]
1it [00:01,  1.56s/it]
2it [00:01,  1.39it/s]
3it [00:01,  2.26it/s]
4it [00:01,  3.14it/s]
5it [00:02,  4.04it/s]
6it [00:02,  5.03it/s]
7it [00:02,  5.93it/s]
8it [00:02,  6.69it/s]
9it [00:02,  7.22it/s]
10it [00:02,  7.80it/s]
11it [00:02,  8.28it/s]
12it [00:02,  8.66it/s]
13it [00:02,  8.88it/s]
14it [00:03,  9.12it/s]
15it [00:03,  9.35it/s]
16it [00:03,  9.39it/s]
17it [00:03,  9.32it/s]
18it [00:03,  9.31it/s]
19it [00:03,  9.15it/s]
20it [00:03,  9.19it/s]
21it [00:03,  9.24it/s]
22it [00:03,  9.35it/s]
23it [00:03,  9.47it/s]
24it [00:04,  9.48it/s]
25it [00:04,  9.44it/s]
26it [00:04,  9.47it/s]
27it [00:04,  9.43it/s]
28it [00:04,  9.54it/s]
29it [00:04,  9.62it/s]
30it [00:04,  9.59it/s]
31it [00:04,  9.57it/s]
32it [00:04,  9.51it/s]
33it [00:05,  9.53it/s]
34it [00:05,  9.52it/s]
35it [00:05,  9.54it/s]
36it [00:05,  9.43it/s]
37it [00:05,  9.46it/s]
reading instances: 1184it [00:05, 301.99it/s]
38it [00:05,  6.20

Validation for0-2000


2001it [04:30, 14.41s/it]
2002it [04:30, 10.12s/it]
reading instances: 64064it [04:30,  3.16it/s]

Results for batch: 2000
batch_number: 2000cs@n: -epoch: 0metrics: {'MRR @10': 0.18259444444444425, 'QueriesRanked': 2000}


2003it [04:30,  7.12s/it]
2004it [04:30,  5.02s/it]
2005it [04:30,  3.55s/it]
2006it [04:30,  2.51s/it]
2007it [04:31,  1.79s/it]
2008it [04:31,  1.28s/it]
2009it [04:31,  1.08it/s]
2010it [04:31,  1.47it/s]
2011it [04:31,  1.96it/s]
2012it [04:31,  2.32it/s]
2013it [04:31,  2.98it/s]
2014it [04:31,  3.76it/s]
2015it [04:32,  4.57it/s]
2016it [04:32,  5.44it/s]
2017it [04:32,  6.23it/s]
2018it [04:32,  6.99it/s]
2019it [04:32,  7.57it/s]
2020it [04:32,  8.04it/s]
2021it [04:32,  8.50it/s]
2022it [04:32,  8.78it/s]
2023it [04:32,  8.69it/s]
2024it [04:32,  8.96it/s]
2025it [04:33,  9.14it/s]
2026it [04:33,  9.22it/s]
2027it [04:33,  9.31it/s]
2028it [04:33,  9.30it/s]
2029it [04:33,  9.26it/s]
2030it [04:33,  9.33it/s]
2031it [04:33,  9.32it/s]
2032it [04:33,  9.36it/s]
2033it [04:33,  9.36it/s]
2034it [04:34,  9.36it/s]
2035it [04:34,  9.17it/s]
2036it [04:34,  9.20it/s]
2037it [04:34,  9.26it/s]
2038it [04:34,  9.13it/s]
2039it [04:34,  9.33it/s]
2040it [04:34,  9.39it/s]
2041it [04:3

...

Results for batch: 2000
batch_number: 2000cs@n: -epoch: 1metrics: {'MRR @10': 0.26589365079365057, 'QueriesRanked': 2000}


2003it [04:45,  7.57s/it]
2004it [04:45,  5.34s/it]
2005it [04:45,  3.77s/it]
2006it [04:45,  2.67s/it]
2007it [04:45,  1.90s/it]
2008it [04:45,  1.36s/it]
2009it [04:45,  1.01it/s]
2010it [04:45,  1.38it/s]
2011it [04:46,  1.85it/s]
2012it [04:46,  2.42it/s]
2013it [04:46,  3.04it/s]
2014it [04:46,  3.69it/s]
2015it [04:46,  4.40it/s]
2016it [04:46,  5.10it/s]
2017it [04:46,  5.62it/s]
2018it [04:46,  6.03it/s]
2019it [04:47,  6.50it/s]
2020it [04:47,  7.14it/s]
2021it [04:47,  7.45it/s]
2022it [04:47,  7.64it/s]
2023it [04:47,  7.98it/s]
2024it [04:47,  8.16it/s]
2025it [04:47,  8.29it/s]
2026it [04:47,  8.56it/s]
2027it [04:47,  8.78it/s]
2028it [04:48,  8.82it/s]
2029it [04:48,  8.85it/s]
2030it [04:48,  8.63it/s]
2031it [04:48,  8.51it/s]
2032it [04:48,  8.82it/s]
2033it [04:48,  8.70it/s]
2034it [04:48,  8.80it/s]
2035it [04:48,  8.50it/s]
2036it [04:49,  8.66it/s]
reading instances: 65152it [04:49, 276.64it/s]
2037it [04:49,  6.18it/s]
2038it [04:49,  6.66it/s]
2039it [04:49,  7

Validation for1-4000
Results for batch: 4000
batch_number: 4000cs@n: -epoch: 1metrics: {'MRR @10': 0.2640845238095235, 'QueriesRanked': 2000}


4003it [09:29,  7.47s/it]
4004it [09:29,  5.27s/it]
4005it [09:29,  3.72s/it]
4006it [09:29,  2.64s/it]
4007it [09:29,  1.88s/it]
4008it [09:29,  1.35s/it]
4009it [09:30,  1.02it/s]
4010it [09:30,  1.39it/s]
4011it [09:30,  1.87it/s]
4012it [09:30,  2.42it/s]
4013it [09:30,  3.11it/s]
4014it [09:30,  3.82it/s]
4015it [09:30,  4.63it/s]
4016it [09:30,  5.46it/s]
4017it [09:30,  6.17it/s]
4018it [09:31,  6.89it/s]
4019it [09:31,  7.44it/s]
4020it [09:31,  7.70it/s]
4021it [09:31,  8.14it/s]
4022it [09:31,  8.42it/s]
4023it [09:31,  8.59it/s]
4024it [09:31,  8.58it/s]
4025it [09:31,  8.65it/s]
4026it [09:31,  8.52it/s]
4027it [09:32,  8.70it/s]
4028it [09:32,  8.81it/s]
4029it [09:32,  8.80it/s]
4030it [09:32,  8.83it/s]
4031it [09:32,  8.99it/s]
4032it [09:32,  9.10it/s]
4033it [09:32,  8.91it/s]
4034it [09:32,  8.18it/s]
4035it [09:32,  7.99it/s]
4036it [09:33,  7.91it/s]
4037it [09:33,  7.78it/s]
4038it [09:33,  7.70it/s]
4039it [09:33,  7.63it/s]
4040it [09:33,  7.61it/s]
4041it [09:3

Validation for1-6000
Results for batch: 6000
batch_number: 6000cs@n: -epoch: 1metrics: {'MRR @10': 0.2639878968253967, 'QueriesRanked': 2000}
early stopping epoch %i batch count %i 1 6000


Eval

Test set **Evaluation** for MSMARCO dataset

In [24]:
PATH_TO_EXECUTION_TIME = Path(f'../output_execution_time/output.txt')
with open(PATH_TO_EXECUTION_TIME, 'a') as f:
    f.write(f'\nIt took: {int(END - START_TIME)} seconds for {model.__class__.__name__} to train')

# do the test and print results
print('Testing the model...')
test_model(model, config, device, 'msmarco')

Testing the model...


0it [00:00, ?it/s]
2it [00:00, 15.66it/s]
reading instances: 256it [00:00, 2064.88it/s]
4it [00:00,  8.77it/s]
6it [00:00, 11.50it/s]
8it [00:00, 13.28it/s]
10it [00:00, 14.89it/s]
12it [00:00, 15.29it/s]
14it [00:01, 15.69it/s]
16it [00:01, 16.30it/s]
18it [00:01, 11.96it/s]
20it [00:01, 12.98it/s]
22it [00:01, 13.91it/s]
24it [00:01, 14.60it/s]
26it [00:01, 15.22it/s]
28it [00:01, 15.44it/s]
reading instances: 3584it [00:01, 1964.72it/s]
30it [00:02, 11.38it/s]
32it [00:02, 12.88it/s]
34it [00:02, 13.88it/s]
36it [00:02, 14.76it/s]
38it [00:02, 15.55it/s]
40it [00:02, 15.51it/s]
42it [00:03, 11.53it/s]
44it [00:03, 12.91it/s]
46it [00:03, 13.73it/s]
48it [00:03, 14.46it/s]
50it [00:03, 15.16it/s]
52it [00:03, 15.38it/s]
reading instances: 6656it [00:03, 1951.95it/s]
54it [00:04, 11.44it/s]
56it [00:04, 12.85it/s]
58it [00:04, 14.21it/s]
60it [00:04, 14.78it/s]
62it [00:04, 15.31it/s]
64it [00:04, 15.87it/s]
66it [00:04, 11.91it/s]
68it [00:04, 12.87it/s]
70it [00:05, 13.89it/s]
72it 

Results from test_model:
MRR @10: 0.2639878968253967 
QueriesRanked: 2000 



{'MRR @10': 0.2639878968253967, 'QueriesRanked': 2000}

In [26]:
# change paths to your data directory
config = {
    "vocab_directory": "/content/drive/My Drive/air-2022-group-06-main/data/allen_vocab_lower_10",
    "pre_trained_embedding": "/content/drive/My Drive/air-2022-group-06-main/data/glove.42B.300d.txt", # we should check this since we are not sure if its the correct file here??
    "model": "conv_knrm",
    "train_data": "/content/drive/My Drive/air-2022-group-06-main/data/triples.train.tsv",
    "validation_data": "/content/drive/My Drive/air-2022-group-06-main/data/msmarco_tuples.test.tsv",
    "test_data":"/content/drive/My Drive/air-2022-group-06-main/data/msmarco_qrels.txt",
}

In [27]:
# do the test and print results
print('Testing the model...')
test_model(model, config, device, 'msmarco')

Testing the model...


0it [00:00, ?it/s]
reading instances: 0it [00:00, ?it/s]
1it [00:00,  2.48it/s]
3it [00:00,  6.71it/s]
reading instances: 385it [00:00, 986.10it/s]
5it [00:00,  6.94it/s]
7it [00:00,  9.29it/s]
9it [00:01, 11.47it/s]
11it [00:01, 12.99it/s]
13it [00:01, 14.33it/s]
15it [00:01, 15.37it/s]
17it [00:01, 16.15it/s]
19it [00:01, 12.17it/s]
21it [00:01, 13.05it/s]
23it [00:01, 14.04it/s]
25it [00:02, 15.05it/s]
27it [00:02, 15.76it/s]
29it [00:02, 16.07it/s]
31it [00:02, 12.11it/s]
33it [00:02, 13.38it/s]
35it [00:02, 14.27it/s]
37it [00:02, 15.25it/s]
39it [00:03, 15.57it/s]
41it [00:03, 15.83it/s]
reading instances: 5248it [00:03, 2026.18it/s]
43it [00:03, 12.05it/s]
45it [00:03, 13.42it/s]
47it [00:03, 14.40it/s]
49it [00:03, 14.94it/s]
51it [00:03, 15.33it/s]
53it [00:04, 15.26it/s]
55it [00:04, 11.49it/s]
57it [00:04, 12.63it/s]
reading instances: 7296it [00:04, 1548.51it/s]
59it [00:04, 13.00it/s]
61it [00:04, 13.73it/s]
63it [00:04, 14.12it/s]
65it [00:04, 14.49it/s]
reading instances

Results from test_model:
MRR @10: 0.25597182539682484 
QueriesRanked: 2000 



{'MRR @10': 0.25597182539682484, 'QueriesRanked': 2000}

Eval for fira-22 baseline label creation

In [30]:
# change paths to your data directory
config = {
    "vocab_directory": "/content/drive/My Drive/air-2022-group-06-main/data/allen_vocab_lower_10",
    "pre_trained_embedding": "/content/drive/My Drive/air-2022-group-06-main/data/glove.42B.300d.txt",
    "model": "conv_knrm",
    "train_data": "/content/drive/My Drive/air-2022-group-06-main/data/triples.train-10k.tsv",
    "validation_data": "/content/drive/My Drive/air-2022-group-06-main/data/msmarco_tuples.validation.tsv",
    "test_data":"/content/drive/My Drive/air-2022-group-06-main/data/fira-22.baseline-qrels.tsv",
}

In [31]:
# do the test and print results
print('Testing the model...')
test_model(model, config, device, 'fira')

Testing the model...


0it [00:00, ?it/s]
2it [00:00, 16.15it/s]
4it [00:00, 16.23it/s]
6it [00:00, 17.43it/s]
8it [00:00, 17.54it/s]
reading instances: 1024it [00:00, 2254.09it/s]
11it [00:00, 18.50it/s]
13it [00:00, 12.61it/s]
15it [00:00, 14.13it/s]
17it [00:01, 15.01it/s]
19it [00:01, 15.98it/s]
21it [00:01, 16.45it/s]
23it [00:01, 16.76it/s]
25it [00:01, 12.47it/s]
27it [00:01, 13.43it/s]
29it [00:01, 14.23it/s]
31it [00:02, 15.21it/s]
33it [00:02, 16.17it/s]
35it [00:02, 16.76it/s]
37it [00:02, 17.29it/s]
reading instances: 4736it [00:02, 2205.93it/s]
39it [00:02, 12.22it/s]
41it [00:02, 13.38it/s]
43it [00:02, 14.49it/s]
45it [00:02, 15.43it/s]
47it [00:03, 15.79it/s]
49it [00:03, 16.29it/s]
51it [00:03, 12.12it/s]
53it [00:03, 13.37it/s]
55it [00:03, 14.44it/s]
57it [00:03, 15.50it/s]
59it [00:03, 16.09it/s]
61it [00:04, 16.29it/s]
reading instances: 7808it [00:04, 2115.47it/s]
63it [00:04, 11.76it/s]
65it [00:04, 13.05it/s]
67it [00:04, 14.12it/s]
69it [00:04, 14.70it/s]
71it [00:04, 15.19it/s]
73it

Results from test_model:
MRR @10: 0.2639878968253967 
QueriesRanked: 2000 



{'MRR @10': 0.2639878968253967, 'QueriesRanked': 2000}

Test Evaluation for FiRA 22- created label from Part 1

In [ ]:
# change paths to your data directory
config = {
    "vocab_directory": "/content/drive/My Drive/air-2022-group-06-main/data/allen_vocab_lower_10",
    "pre_trained_embedding": "/content/drive/My Drive/air-2022-group-06-main/data/glove.42B.300d.txt", 
    "model": "conv_knrm",
    "train_data": "/content/drive/My Drive/air-2022-group-06-main/data/triples.train.tsv",
    "validation_data": "/content/drive/My Drive/air-2022-group-06-main/data/msmarco_tuples.validation.tsv",
    "test_data":"/content/drive/My Drive/air-2022-group-06-main/data/qrels_preprocessed.tsv",
}

In [ ]:
# do the test and print results
print('Testing the model...')
test_model(model, config, device, 'fira')

Testing the model...


0it [00:00, ?it/s]
2it [00:00, 16.15it/s]
4it [00:00, 16.23it/s]
6it [00:00, 17.43it/s]
8it [00:00, 17.54it/s]
reading instances: 1024it [00:00, 2254.09it/s]
11it [00:00, 18.50it/s]
13it [00:00, 12.61it/s]
15it [00:00, 14.13it/s]
17it [00:01, 15.01it/s]
19it [00:01, 15.98it/s]
21it [00:01, 16.45it/s]
23it [00:01, 16.76it/s]
25it [00:01, 12.47it/s]
27it [00:01, 13.43it/s]
29it [00:01, 14.23it/s]
31it [00:02, 15.21it/s]
33it [00:02, 16.17it/s]
35it [00:02, 16.76it/s]
37it [00:02, 17.29it/s]
reading instances: 4736it [00:02, 2205.93it/s]
39it [00:02, 12.22it/s]
41it [00:02, 13.38it/s]
43it [00:02, 14.49it/s]
45it [00:02, 15.43it/s]
47it [00:03, 15.79it/s]
49it [00:03, 16.29it/s]
51it [00:03, 12.12it/s]
53it [00:03, 13.37it/s]
55it [00:03, 14.44it/s]
57it [00:03, 15.50it/s]
59it [00:03, 16.09it/s]
61it [00:04, 16.29it/s]
reading instances: 7808it [00:04, 2115.47it/s]
63it [00:04, 11.76it/s]
65it [00:04, 13.05it/s]
67it [00:04, 14.12it/s]
69it [00:04, 14.70it/s]
71it [00:04, 15.19it/s]
73it

Results from test_model:
MRR @10: 0.2639878968253967 
QueriesRanked: 2000 



{'MRR @10': 0.2639878968253967, 'QueriesRanked': 2000}